In [35]:
import pandas as pd
import glob
import numpy
import csv
from nltk.tokenize import word_tokenize
import xlrd
import re
from nltk import bigrams
from nltk import ngrams
import operator
from collections import Counter
from nltk.corpus import stopwords
import string
import matplotlib.pyplot as plt

In [36]:
from random import randint
from numpy import array
from numpy import argmax
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Dense

In [37]:
path = r'E:\Level 4 Project\dataset\final\preprocess' # use your path
all_files = glob.glob(path + "/*.csv")

In [38]:
li = []

In [39]:
for filename in all_files:
    df = pd.read_csv(filename, index_col=None, header=0)
    li.append(df)

In [40]:
df = pd.concat(li, axis=0, ignore_index=True, sort=False)

In [41]:
df.head()

Date  \
0  2014-01-01 23:59:47+00:00    
1  2014-01-01 23:57:47+00:00    
2  2014-01-01 23:56:21+00:00    
3  2014-01-01 23:56:03+00:00    
4  2014-01-01 23:55:55+00:00    

                                                Text Text   
0   Clearwater Beach,FL Scattered Thunderstorms t...   NaN  
1   Tourism disappeared because of Troubles: To...   NaN  
2   I'm at Department of Tourism and Hospitality ...   NaN  
3   'Like a Napa Valley wine tour': Pot tourism r...   NaN  
4           Focus : Recreation & Tourism Planning .    NaN

In [42]:
df.shape

(5492006, 3)

In [43]:
emoticons_str = r"""
    (?:
        [:=;] # Eyes
        [oO\-]? # Nose (optional)
        [D\)\]\(\]/\\OpP] # Mouth
    )"""

In [44]:
def preprocess_fornothash(s, lowercase=True):
    tokens = tokenize_fornothash(s)
    if lowercase:
        tokens = [token if emoticon_re.search(token) else token.lower() for token in tokens]
    return tokens

def tokenize_fornothash(s):
    return tokens_re_fornothash.findall(s)


regex_str_fornothash = [
    emoticons_str,
    r'<[^>]+>',  # HTML tags
    r'(?:@[\w_]+)',  # @-mentions
    #r"(?:\#+[\w_]+[\w\'_\-]*[\w_]+)",  # hash-tags
    r'http[s]?://(?:[a-z]|[0-9]|[$-_@.&amp;+]|[!*\(\),]|(?:%[0-9a-f][0-9a-f]))+',  # URLs

    r'(?:(?:\d+,?)+(?:\.?\d+)?)',  # numbers
    r"(?:[a-z][a-z'\-_]+[a-z])",  # words with - and '
    r'(?:[\w_]+)',  # other words
    r'(?:\S)'  # anything else
]

tokens_re_fornothash = re.compile(r'(' + '|'.join(regex_str_fornothash) + ')', re.VERBOSE | re.IGNORECASE)
emoticon_re = re.compile(r'^' + emoticons_str + '$', re.VERBOSE | re.IGNORECASE)

In [45]:
def preprocess_forhash(s, lowercase=True):
    tokens = tokenize_forhash(s)
    if lowercase:
        tokens = [token if emoticon_re.search(token) else token.lower() for token in tokens]
    return tokens

def tokenize_forhash(s):
    return tokens_re_forhash.findall(s)

regex_str_forhash = [
    emoticons_str,
    r'<[^>]+>',  # HTML tags
    r'(?:@[\w_]+)',  # @-mentions
    r"(?:\#+[\w_]+[\w\'_\-]*[\w_]+)",  # hash-tags
    r'http[s]?://(?:[a-z]|[0-9]|[$-_@.&amp;+]|[!*\(\),]|(?:%[0-9a-f][0-9a-f]))+',  # URLs

    r'(?:(?:\d+,?)+(?:\.?\d+)?)',  # numbers
    r"(?:[a-z][a-z'\-_]+[a-z])",  # words with - and '
    r'(?:[\w_]+)',  # other words
    r'(?:\S)'  # anything else
]

tokens_re_forhash = re.compile(r'(' + '|'.join(regex_str_forhash) + ')', re.VERBOSE | re.IGNORECASE)
emoticon_re = re.compile(r'^' + emoticons_str + '$', re.VERBOSE | re.IGNORECASE)

In [46]:
punctuation = list(string.punctuation)
unnecssary = ['The','tourism','I','rt', 'via','...','â','click']
unnecssary_hash = ['#','#tourism']
ascii_words = ['\x92','\x96']
years = ['2018','2017','2016','2015','2014','2013']
numbers = ['nine']
stop = stopwords.words('english') + punctuation + unnecssary + ascii_words + years + unnecssary_hash + numbers

count_all = []
popular_common_words = []
i=0
sets=2000

c =0
for x in range(sets):
    count_all.append(Counter())

for y in range(sets):
    for x in range(1, 500):
        value = df.loc[i, "Text"]

        #terms_all = [term for term in preprocess_fornothash(value) if term not in stop]  
        terms_all = [term for term in preprocess_forhash(value)
                  if term.startswith('#') if term not in stop]
        i = i + 1
        count_all[y].update(terms_all)
    
    popular_common_words.append(count_all[y].most_common(5))
        

In [47]:
trendingTopicsAll = []

def processTrendingArray(str):
    global trendingTopicsAll
    b = [i for i,x in enumerate(trendingTopicsAll) if x == str]
    if(b == []):
        trendingTopicsAll.append(str)
        return len(trendingTopicsAll)-1
    else:
        return b[0]

In [48]:
trendingTopicsInEachDays = []
trendingIdsInEachDays = []
for index, y in enumerate(popular_common_words):
    trendingTopicsInEachDays.append([])
    trendingIdsInEachDays.append([])
    for x in y:
        trendingTopicsInEachDays[index].append(x[0])
        trendingIdsInEachDays[index].append(processTrendingArray(x[0]))
        

# print(trendingTopicsInEachDays)
# print("####################")
print(trendingTopicsAll)
# print("####################")
# print(trendingIdsInEachDays)

['#travel', '#news', '#amsterdam', '#netherlands', '#holland', '#smtravel', '#trip', '#photo', '#marijuana', '#travelers', '#latestnews', '#street', '#htmi', '#colorado', '#pakistan', '#adventure', '#maldives', '#town', '#road', '#jobs', '#aglasem', '#infografia', '#infographic', '#googlenews', '#webdesign', '#vatican', '#popefrancis', '#business', '#amazing', '#chile', '#ttot', '#hhi', '#cnn', '#culture', '#carrefour', '#muscat', '#egypt', '#blog', '#saveswedenswolves', '#backpacking', '#welcome_to_egypt', '#alanailham', '#thailand', '#vmy2014', '#haiti', '#photography', '#church', '#southafrica', '#qatar', '#malaysia', '#hospitality', '#hotels', '#food', '#neworleanswill', '#cruisepeople', '#ofc14', '#china', '#rwanda', '#ecuador', '#keepwolveslisted', '#nysos14', '#expediachat', '#africa', '#job', '#tech', '#socialmedia', '#mashable', '#gdaytourism', '#ireland', '#hampi', '#uganda', '#scotlandhour', '#twitter', '#marketing', '#talent4hire', '#sayfie', '#ff', '#oman', '#caribbean', '

In [50]:
# generate a sequence of random numbers in [0, 99]
tweetIdsCount = -1
inputs = len(trendingTopicsAll)

def generate_sequence():
    global tweetIdsCount
    print("tweetIdsCount - ",tweetIdsCount)
    tweetIdsCount = tweetIdsCount+1
    return (trendingIdsInEachDays[tweetIdsCount])
    #return [23,12,45]
    
# one hot encode sequence
def one_hot_encode(sequence, n_unique=inputs):
	encoding = list()
	for value in sequence:
		vector = [0 for _ in range(n_unique)]
		vector[value] = 1
		encoding.append(vector)
	return array(encoding)
 
# decode a one hot encoded string
def one_hot_decode(encoded_seq):
	return [argmax(vector) for vector in encoded_seq]
 
# generate data for the lstm
def generate_data():
	# generate sequence
	sequence = generate_sequence()
	# one hot encode
	encoded = one_hot_encode(sequence)
	# convert to 3d for input
	X = encoded.reshape(encoded.shape[0], 1, encoded.shape[1])
	return X, encoded    
    
# define model
model = Sequential() 
model.add(LSTM(50, input_shape=(1, inputs)))
model.add(Dense(inputs, activation='relu'))
model.add(Dense(inputs, activation='softmax'))
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
# fit model
for i in range(1500):
	X, y = generate_data()
	model.fit(X, y, epochs=40, batch_size=1, verbose=2)
# evaluate model on new data
X, y = generate_data()
yhat = model.predict(X)

#print('Expected:  %s' % one_hot_decode(y))
#print('Predicted: %s' % one_hot_decode(yhat))

a = []
b = []
i = 0;
# for x in range(5):
#     if(one_hot_decode(y)[x] == one_hot_decode(yhat)[x]):
#         i += 1
#     a.append(trendingTopicsAll[one_hot_decode(y)[x]])
#     b.append(trendingTopicsAll[one_hot_decode(yhat)[x]])
   
# print("Expected: ",a)
# print("Predicted: ",b)
# print("Test Accuracy: ",(i/5)*100)

tweetIdsCount -  -1
Epoch 1/40
5/5 - 3s - loss: 7.2585 - acc: 0.0000e+00
Epoch 2/40
5/5 - 0s - loss: 7.2124 - acc: 0.4000
Epoch 3/40
5/5 - 0s - loss: 7.1583 - acc: 0.6000
Epoch 4/40
5/5 - 0s - loss: 7.0736 - acc: 0.8000
Epoch 5/40
5/5 - 0s - loss: 6.9492 - acc: 1.0000
Epoch 6/40
5/5 - 0s - loss: 6.7604 - acc: 1.0000
Epoch 7/40
5/5 - 0s - loss: 6.4808 - acc: 1.0000
Epoch 8/40
5/5 - 0s - loss: 6.0850 - acc: 0.8000
Epoch 9/40
5/5 - 0s - loss: 5.5088 - acc: 0.6000
Epoch 10/40
5/5 - 0s - loss: 4.7111 - acc: 0.6000
Epoch 11/40
5/5 - 0s - loss: 3.6765 - acc: 0.6000
Epoch 12/40
5/5 - 0s - loss: 2.5379 - acc: 0.6000
Epoch 13/40
5/5 - 0s - loss: 1.7876 - acc: 0.2000
Epoch 14/40
5/5 - 0s - loss: 1.5677 - acc: 0.6000
Epoch 15/40
5/5 - 0s - loss: 1.5269 - acc: 0.6000
Epoch 16/40
5/5 - 0s - loss: 1.4862 - acc: 0.8000
Epoch 17/40
5/5 - 0s - loss: 1.4642 - acc: 1.0000
Epoch 18/40
5/5 - 0s - loss: 1.4367 - acc: 0.8000
Epoch 19/40
5/5 - 0s - loss: 1.4207 - acc: 1.0000
Epoch 20/40
5/5 - 0s - loss: 1.3797

Epoch 4/40
5/5 - 0s - loss: 0.1170 - acc: 1.0000
Epoch 5/40
5/5 - 0s - loss: 0.0781 - acc: 1.0000
Epoch 6/40
5/5 - 0s - loss: 0.0684 - acc: 1.0000
Epoch 7/40
5/5 - 0s - loss: 0.0497 - acc: 1.0000
Epoch 8/40
5/5 - 0s - loss: 0.0452 - acc: 1.0000
Epoch 9/40
5/5 - 0s - loss: 0.0375 - acc: 1.0000
Epoch 10/40
5/5 - 0s - loss: 0.0325 - acc: 1.0000
Epoch 11/40
5/5 - 0s - loss: 0.0281 - acc: 1.0000
Epoch 12/40
5/5 - 0s - loss: 0.0245 - acc: 1.0000
Epoch 13/40
5/5 - 0s - loss: 0.0219 - acc: 1.0000
Epoch 14/40
5/5 - 0s - loss: 0.0198 - acc: 1.0000
Epoch 15/40
5/5 - 0s - loss: 0.0175 - acc: 1.0000
Epoch 16/40
5/5 - 0s - loss: 0.0161 - acc: 1.0000
Epoch 17/40
5/5 - 0s - loss: 0.0145 - acc: 1.0000
Epoch 18/40
5/5 - 0s - loss: 0.0133 - acc: 1.0000
Epoch 19/40
5/5 - 0s - loss: 0.0122 - acc: 1.0000
Epoch 20/40
5/5 - 0s - loss: 0.0111 - acc: 1.0000
Epoch 21/40
5/5 - 0s - loss: 0.0104 - acc: 1.0000
Epoch 22/40
5/5 - 0s - loss: 0.0095 - acc: 1.0000
Epoch 23/40
5/5 - 0s - loss: 0.0088 - acc: 1.0000
Epoch 

5/5 - 0s - loss: 1.4998 - acc: 0.6000
Epoch 8/40
5/5 - 0s - loss: 1.0442 - acc: 0.6000
Epoch 9/40
5/5 - 0s - loss: 0.8122 - acc: 0.6000
Epoch 10/40
5/5 - 0s - loss: 0.4908 - acc: 0.8000
Epoch 11/40
5/5 - 0s - loss: 0.3261 - acc: 0.8000
Epoch 12/40
5/5 - 0s - loss: 0.2807 - acc: 1.0000
Epoch 13/40
5/5 - 0s - loss: 0.2888 - acc: 0.8000
Epoch 14/40
5/5 - 0s - loss: 0.2764 - acc: 0.8000
Epoch 15/40
5/5 - 0s - loss: 0.2346 - acc: 1.0000
Epoch 16/40
5/5 - 0s - loss: 0.2130 - acc: 1.0000
Epoch 17/40
5/5 - 0s - loss: 0.1927 - acc: 1.0000
Epoch 18/40
5/5 - 0s - loss: 0.1877 - acc: 1.0000
Epoch 19/40
5/5 - 0s - loss: 0.1468 - acc: 1.0000
Epoch 20/40
5/5 - 0s - loss: 0.1116 - acc: 1.0000
Epoch 21/40
5/5 - 0s - loss: 0.0946 - acc: 1.0000
Epoch 22/40
5/5 - 0s - loss: 0.0675 - acc: 1.0000
Epoch 23/40
5/5 - 0s - loss: 0.0553 - acc: 1.0000
Epoch 24/40
5/5 - 0s - loss: 0.0423 - acc: 1.0000
Epoch 25/40
5/5 - 0s - loss: 0.0347 - acc: 1.0000
Epoch 26/40
5/5 - 0s - loss: 0.0284 - acc: 1.0000
Epoch 27/40
5/

5/5 - 0s - loss: 8.0450e-04 - acc: 1.0000
Epoch 11/40
5/5 - 0s - loss: 7.7796e-04 - acc: 1.0000
Epoch 12/40
5/5 - 0s - loss: 7.5892e-04 - acc: 1.0000
Epoch 13/40
5/5 - 0s - loss: 7.3357e-04 - acc: 1.0000
Epoch 14/40
5/5 - 0s - loss: 7.1558e-04 - acc: 1.0000
Epoch 15/40
5/5 - 0s - loss: 6.9839e-04 - acc: 1.0000
Epoch 16/40
5/5 - 0s - loss: 6.7882e-04 - acc: 1.0000
Epoch 17/40
5/5 - 0s - loss: 6.6609e-04 - acc: 1.0000
Epoch 18/40
5/5 - 0s - loss: 6.5537e-04 - acc: 1.0000
Epoch 19/40
5/5 - 0s - loss: 6.3459e-04 - acc: 1.0000
Epoch 20/40
5/5 - 0s - loss: 6.2009e-04 - acc: 1.0000
Epoch 21/40
5/5 - 0s - loss: 6.1192e-04 - acc: 1.0000
Epoch 22/40
5/5 - 0s - loss: 5.9106e-04 - acc: 1.0000
Epoch 23/40
5/5 - 0s - loss: 5.7646e-04 - acc: 1.0000
Epoch 24/40
5/5 - 0s - loss: 5.6453e-04 - acc: 1.0000
Epoch 25/40
5/5 - 0s - loss: 5.4905e-04 - acc: 1.0000
Epoch 26/40
5/5 - 0s - loss: 5.3788e-04 - acc: 1.0000
Epoch 27/40
5/5 - 0s - loss: 5.2679e-04 - acc: 1.0000
Epoch 28/40
5/5 - 0s - loss: 5.1171e-04 

Epoch 11/40
5/5 - 0s - loss: 0.4467 - acc: 1.0000
Epoch 12/40
5/5 - 0s - loss: 0.3456 - acc: 1.0000
Epoch 13/40
5/5 - 0s - loss: 0.2658 - acc: 1.0000
Epoch 14/40
5/5 - 0s - loss: 0.2291 - acc: 1.0000
Epoch 15/40
5/5 - 0s - loss: 0.1992 - acc: 1.0000
Epoch 16/40
5/5 - 0s - loss: 0.1665 - acc: 1.0000
Epoch 17/40
5/5 - 0s - loss: 0.1523 - acc: 1.0000
Epoch 18/40
5/5 - 0s - loss: 0.1126 - acc: 1.0000
Epoch 19/40
5/5 - 0s - loss: 0.0899 - acc: 1.0000
Epoch 20/40
5/5 - 0s - loss: 0.0608 - acc: 1.0000
Epoch 21/40
5/5 - 0s - loss: 0.0421 - acc: 1.0000
Epoch 22/40
5/5 - 0s - loss: 0.0295 - acc: 1.0000
Epoch 23/40
5/5 - 0s - loss: 0.0200 - acc: 1.0000
Epoch 24/40
5/5 - 0s - loss: 0.0167 - acc: 1.0000
Epoch 25/40
5/5 - 0s - loss: 0.0133 - acc: 1.0000
Epoch 26/40
5/5 - 0s - loss: 0.0115 - acc: 1.0000
Epoch 27/40
5/5 - 0s - loss: 0.0091 - acc: 1.0000
Epoch 28/40
5/5 - 0s - loss: 0.0077 - acc: 1.0000
Epoch 29/40
5/5 - 0s - loss: 0.0068 - acc: 1.0000
Epoch 30/40
5/5 - 0s - loss: 0.0057 - acc: 1.0000


...

Epoch 13/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 14/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 15/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 16/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 17/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 18/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 19/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 20/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 21/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 22/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 23/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 24/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 25/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 26/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 27/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 28/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 29/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 30/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 31/40
5/5 - 0s - loss:

Epoch 10/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 11/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 12/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 13/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 14/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 15/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 16/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 17/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 18/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 19/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 20/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 21/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 22/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 23/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 24/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 25/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 26/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 27/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 28/40
5/5 - 0s - loss:

tweetIdsCount -  1488
Epoch 1/40
5/5 - 0s - loss: 3.8852 - acc: 0.8000
Epoch 2/40
5/5 - 0s - loss: 3.4216 - acc: 0.8000
Epoch 3/40
5/5 - 0s - loss: 2.4441 - acc: 0.8000
Epoch 4/40
5/5 - 0s - loss: 1.8963 - acc: 0.8000
Epoch 5/40
5/5 - 0s - loss: 1.4501 - acc: 0.8000
Epoch 6/40
5/5 - 0s - loss: 0.9031 - acc: 0.8000
Epoch 7/40
5/5 - 0s - loss: 0.5613 - acc: 0.8000
Epoch 8/40
5/5 - 0s - loss: 0.2917 - acc: 1.0000
Epoch 9/40
5/5 - 0s - loss: 0.0195 - acc: 1.0000
Epoch 10/40
5/5 - 0s - loss: 0.0054 - acc: 1.0000
Epoch 11/40
5/5 - 0s - loss: 0.0015 - acc: 1.0000
Epoch 12/40
5/5 - 0s - loss: 8.4624e-04 - acc: 1.0000
Epoch 13/40
5/5 - 0s - loss: 5.8349e-04 - acc: 1.0000
Epoch 14/40
5/5 - 0s - loss: 4.1197e-04 - acc: 1.0000
Epoch 15/40
5/5 - 0s - loss: 3.3920e-04 - acc: 1.0000
Epoch 16/40
5/5 - 0s - loss: 3.1854e-04 - acc: 1.0000
Epoch 17/40
5/5 - 0s - loss: 2.8945e-04 - acc: 1.0000
Epoch 18/40
5/5 - 1s - loss: 2.8154e-04 - acc: 1.0000
Epoch 19/40
5/5 - 0s - loss: 2.7178e-04 - acc: 1.0000
Epoch

Epoch 36/40
5/5 - 0s - loss: 0.0018 - acc: 1.0000
Epoch 37/40
5/5 - 0s - loss: 0.0016 - acc: 1.0000
Epoch 38/40
5/5 - 0s - loss: 0.0015 - acc: 1.0000
Epoch 39/40
5/5 - 0s - loss: 0.0015 - acc: 1.0000
Epoch 40/40
5/5 - 0s - loss: 0.0014 - acc: 1.0000
tweetIdsCount -  1492
Epoch 1/40
5/5 - 0s - loss: 1.1921e-06 - acc: 1.0000
Epoch 2/40
5/5 - 0s - loss: 2.3842e-08 - acc: 1.0000
Epoch 3/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 4/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 5/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 6/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 7/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 8/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 9/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 10/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 11/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 12/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 13/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 14/40
5/5 - 0s - loss: 0.0000

Epoch 28/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 29/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 30/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 31/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 32/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 33/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 34/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 35/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 36/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 37/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 38/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 39/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 40/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
tweetIdsCount -  1496
Epoch 1/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 2/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 3/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 4/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 5/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 6/40


In [53]:
print(tweetIdsCount)
testaccuracy = []
tweetIdsCount = 1500

def getOneAccuracy(a,b):
    i = 0;
    for x in range(5):
        if(a[x] == b[x]):
            i += 1
    return i/5

def getTestData():
    for i in range(490):
        X, y = generate_data()
        yhat = model.predict(X)
        print('Expected:  %s' % one_hot_decode(y))
        print('Predicted: %s' % one_hot_decode(yhat))
        testaccuracy.append(getOneAccuracy(one_hot_decode(y),one_hot_decode(yhat)))
    
getTestData()
print(testaccuracy)
print('average - ',sum(testaccuracy) / len(testaccuracy))

2001
tweetIdsCount -  1500
Expected:  [0, 1078, 1, 230, 30]
Predicted: [0, 981, 1, 230, 30]
tweetIdsCount -  1501
Expected:  [0, 1079, 1, 1080, 934]
Predicted: [0, 385, 1, 1077, 934]
tweetIdsCount -  1502
Expected:  [0, 734, 1, 1081, 348]
Predicted: [0, 734, 1, 8, 348]
tweetIdsCount -  1503
Expected:  [0, 1082, 734, 703, 1]
Predicted: [0, 21, 734, 123, 1]
tweetIdsCount -  1504
Expected:  [0, 780, 311, 405, 602]
Predicted: [0, 780, 311, 405, 602]
tweetIdsCount -  1505
Expected:  [0, 643, 1, 27, 1082]
Predicted: [0, 643, 1, 27, 21]
tweetIdsCount -  1506
Expected:  [0, 1082, 102, 101, 663]
Predicted: [0, 21, 102, 101, 663]
tweetIdsCount -  1507
Expected:  [0, 1082, 48, 101, 1004]
Predicted: [0, 21, 49, 101, 1004]
tweetIdsCount -  1508
Expected:  [0, 1, 36, 1083, 1084]
Predicted: [0, 1, 36, 537, 385]
tweetIdsCount -  1509
Expected:  [0, 1085, 311, 1, 348]
Predicted: [0, 385, 311, 1, 348]
tweetIdsCount -  1510
Expected:  [0, 1086, 45, 36, 1]
Predicted: [0, 1077, 45, 36, 1]
tweetIdsCount -  

Expected:  [0, 566, 74, 134, 833]
Predicted: [0, 566, 348, 134, 833]
tweetIdsCount -  1593
Expected:  [0, 1, 1117, 81, 348]
Predicted: [0, 1, 385, 81, 348]
tweetIdsCount -  1594
Expected:  [0, 1, 1117, 1118, 1119]
Predicted: [0, 1, 385, 854, 1077]
tweetIdsCount -  1595
Expected:  [0, 1120, 1121, 36, 1116]
Predicted: [0, 385, 385, 36, 791]
tweetIdsCount -  1596
Expected:  [0, 1122, 239, 558, 1116]
Predicted: [0, 1070, 1042, 558, 791]
tweetIdsCount -  1597
Expected:  [0, 1123, 1124, 80, 794]
Predicted: [0, 21, 385, 80, 794]
tweetIdsCount -  1598
Expected:  [0, 101, 833, 936, 937]
Predicted: [0, 101, 833, 936, 937]
tweetIdsCount -  1599
Expected:  [0, 80, 101, 348, 1]
Predicted: [0, 80, 101, 348, 1]
tweetIdsCount -  1600
Expected:  [0, 80, 794, 91, 134]
Predicted: [0, 80, 794, 91, 134]
tweetIdsCount -  1601
Expected:  [0, 1125, 1126, 33, 1127]
Predicted: [0, 1077, 285, 33, 1076]
tweetIdsCount -  1602
Expected:  [0, 80, 1128, 1, 1129]
Predicted: [0, 80, 385, 1, 1076]
tweetIdsCount -  1603


Expected:  [0, 991, 64, 1192, 1197]
Predicted: [0, 0, 64, 385, 385]
tweetIdsCount -  1696
Expected:  [0, 65, 512, 81, 902]
Predicted: [0, 65, 981, 81, 902]
tweetIdsCount -  1697
Expected:  [0, 21, 22, 65, 991]
Predicted: [0, 21, 22, 65, 0]
tweetIdsCount -  1698
Expected:  [991, 0, 1193, 812, 1]
Predicted: [0, 0, 385, 812, 1]
tweetIdsCount -  1699
Expected:  [991, 0, 1193, 21, 22]
Predicted: [0, 0, 385, 21, 22]
tweetIdsCount -  1700
Expected:  [991, 1193, 0, 21, 22]
Predicted: [0, 385, 0, 21, 22]
tweetIdsCount -  1701
Expected:  [991, 1193, 0, 1198, 1199]
Predicted: [0, 385, 0, 385, 1076]
tweetIdsCount -  1702
Expected:  [0, 928, 241, 1200, 1]
Predicted: [0, 1077, 241, 402, 1]
tweetIdsCount -  1703
Expected:  [0, 22, 21, 285, 928]
Predicted: [0, 22, 21, 285, 1077]
tweetIdsCount -  1704
Expected:  [1201, 0, 1202, 45, 1203]
Predicted: [385, 0, 385, 45, 791]
tweetIdsCount -  1705
Expected:  [0, 928, 241, 1204, 285]
Predicted: [0, 1077, 241, 21, 285]
tweetIdsCount -  1706
Expected:  [0, 991

Expected:  [0, 102, 108, 6, 1273]
Predicted: [0, 102, 108, 6, 385]
tweetIdsCount -  1792
Expected:  [0, 64, 66, 1274, 1]
Predicted: [0, 64, 66, 285, 1]
tweetIdsCount -  1793
Expected:  [0, 944, 1275, 989, 907]
Predicted: [0, 1077, 8, 385, 853]
tweetIdsCount -  1794
Expected:  [0, 1, 1276, 948, 1277]
Predicted: [0, 1, 385, 910, 1077]
tweetIdsCount -  1795
Expected:  [0, 104, 794, 607, 833]
Predicted: [0, 104, 794, 607, 833]
tweetIdsCount -  1796
Expected:  [0, 62, 1278, 1279, 1]
Predicted: [0, 62, 1077, 385, 1]
tweetIdsCount -  1797
Expected:  [0, 925, 1280, 132, 984]
Predicted: [0, 925, 1076, 132, 984]
tweetIdsCount -  1798
Expected:  [0, 73, 134, 50, 319]
Predicted: [0, 73, 134, 50, 319]
tweetIdsCount -  1799
Expected:  [0, 1281, 56, 1282, 21]
Predicted: [0, 385, 56, 385, 21]
tweetIdsCount -  1800
Expected:  [0, 56, 1282, 1283, 102]
Predicted: [0, 56, 385, 814, 102]
tweetIdsCount -  1801
Expected:  [0, 1283, 319, 56, 1264]
Predicted: [0, 814, 319, 56, 1076]
tweetIdsCount -  1802
Expec

Expected:  [0, 36, 45, 545, 547]
Predicted: [0, 36, 45, 545, 547]
tweetIdsCount -  1890
Expected:  [0, 102, 547, 602, 108]
Predicted: [0, 102, 547, 602, 108]
tweetIdsCount -  1891
Expected:  [0, 547, 50, 730, 80]
Predicted: [0, 547, 50, 730, 80]
tweetIdsCount -  1892
Expected:  [0, 311, 730, 780, 814]
Predicted: [0, 311, 730, 780, 814]
tweetIdsCount -  1893
Expected:  [0, 730, 132, 230, 391]
Predicted: [0, 730, 132, 230, 391]
tweetIdsCount -  1894
Expected:  [0, 730, 132, 134, 27]
Predicted: [0, 730, 132, 134, 27]
tweetIdsCount -  1895
Expected:  [0, 230, 1349, 102, 1]
Predicted: [0, 230, 8, 102, 1]
tweetIdsCount -  1896
Expected:  [0, 547, 545, 107, 50]
Predicted: [0, 547, 545, 107, 50]
tweetIdsCount -  1897
Expected:  [0, 547, 545, 107, 348]
Predicted: [0, 547, 545, 107, 348]
tweetIdsCount -  1898
Expected:  [0, 893, 786, 547, 102]
Predicted: [0, 402, 722, 547, 102]
tweetIdsCount -  1899
Expected:  [0, 941, 1350, 1351, 239]
Predicted: [0, 791, 385, 285, 1042]
tweetIdsCount -  1900
Ex

Expected:  [0, 1402, 62, 1403, 1404]
Predicted: [0, 385, 62, 791, 385]
tweetIdsCount -  1982
Expected:  [0, 730, 64, 323, 107]
Predicted: [0, 730, 64, 107, 107]
tweetIdsCount -  1983
Expected:  [0, 1405, 107, 132, 1406]
Predicted: [0, 8, 107, 132, 285]
tweetIdsCount -  1984
Expected:  [0, 1407, 1405, 545, 1]
Predicted: [0, 385, 8, 545, 1]
tweetIdsCount -  1985
Expected:  [0, 1407, 734, 794, 730]
Predicted: [0, 385, 734, 794, 730]
tweetIdsCount -  1986
Expected:  [0, 1407, 1406, 780, 311]
Predicted: [0, 385, 285, 780, 311]
tweetIdsCount -  1987
Expected:  [0, 311, 780, 1406, 132]
Predicted: [0, 311, 780, 285, 132]
tweetIdsCount -  1988
Expected:  [0, 1406, 1408, 833, 1]
Predicted: [0, 285, 385, 833, 1]
tweetIdsCount -  1989
Expected:  [0, 730, 1, 1409, 1410]
Predicted: [0, 730, 1, 1076, 8]
[0.8, 0.6, 0.8, 0.6, 1.0, 0.8, 0.8, 0.6, 0.6, 0.8, 0.8, 0.8, 0.6, 0.6, 0.6, 1.0, 1.0, 1.0, 1.0, 0.4, 0.8, 0.6, 0.8, 1.0, 1.0, 1.0, 0.8, 0.4, 0.4, 0.6, 0.6, 0.6, 0.8, 0.6, 0.6, 0.6, 0.8, 1.0, 0.2, 0.4,

In [ ]:
len(trendingTopicsAll)